In [0]:
from pyspark.sql.functions import *
from pyspark.sql.window import Window

In [0]:
display(dbutils.fs.ls("FileStore/tables"))

path name size modificationTime dbfs:/FileStore/tables/superstore.csv superstore.csv 15844267 1744723067000 dbfs:/FileStore/tables/superstore_ano/ superstore_ano/ 0 0 dbfs:/FileStore/tables/superstore_mes/ superstore_mes/ 0 0

In [0]:
%sql

CREATE DATABASE IF NOT EXISTS BRONZE;
CREATE DATABASE IF NOT EXISTS SILVER;
CREATE DATABASE IF NOT EXISTS GOLD;

In [0]:
df = spark.read.option("header", True).option("multiLine", True).option("escape", "\"").option("quote", "\"").option("delimiter", ",").csv("dbfs:/FileStore/tables/superstore.csv")

display(df)

Category City Country Customer.ID Customer.Name Discount Market 记录数 Order.Date Order.ID Order.Priority Product.ID Product.Name Profit Quantity Region Row.ID Sales Segment Ship.Date Ship.Mode Shipping.Cost State Sub.Category Year Market2 weeknum Office Supplies Los Angeles United States LS-172304 Lycoris Saunders 0 US 1 2011-01-07 00:00:00.000 CA-2011-130813 High OFF-PA-10002005 Xerox 225 9.3312 3 West 36624 19 Consumer 2011-01-09 00:00:00.000 Second Class 4.37 California Paper 2011 North America 2 Office Supplies Los Angeles United States MV-174854 Mark Van Huff 0 US 1 2011-01-21 00:00:00.000 CA-2011-148614 Medium OFF-PA-10002893 Wirebound Service Call Books, 5 1/2" x 4" 9.2928 2 West 37033 19 Consumer 2011-01-26 00:00:00.000 Standard Class 0.94 California Paper 2011 North America 4 Office Supplies Los Angeles United States CS-121304 Chad Sievert 0 US 1 2011-08-05 00:00:00.000 CA-2011-118962 Medium OFF-PA-10000659 Adams Phone Message Book, Professional, 400 Message Capacity, 5 3/6” x 11” 9.8418 3 West 31468 21 Consumer 2011-08-09 00:00:00.000 Standard Class 1.81 California Paper 2011 North America 32 Office Supplies Los Angeles United States CS-121304 Chad Sievert 0 US 1 2011-08-05 00:00:00.000 CA-2011-118962 Medium OFF-PA-10001144 Xerox 1913 53.2608 2 West 31469 111 Consumer 2011-08-09 00:00:00.000 Standard Class 4.59 California Paper 2011 North America 32 Office Supplies Los Angeles United States AP-109154 Arthur Prichep 0 US 1 2011-09-29 00:00:00.000 CA-2011-146969 High OFF-PA-10002105 Xerox 223 3.1104 1 West 32440 6 Consumer 2011-10-03 00:00:00.000 Standard Class 1.32 California Paper 2011 North America 40 Office Supplies Los Angeles United States JF-154904 Jeremy Farry 0 US 1 2011-10-19 00:00:00.000 CA-2011-117317 Critical OFF-PA-10004519 Spiral Phone Message Books with Labels by Adams 6.5856 3 West 32890 13 Consumer 2011-10-19 00:00:00.000 Same Day 2.39 California Paper 2011 North America 43 Office Supplies Los Angeles United States WB-218504 William Brown 0 US 1 2011-11-04 00:00:00.000 CA-2011-125829 Medium OFF-PA-10000223 Xerox 2000 9.3312 3 West 35608 19 Consumer 2011-11-11 00:00:00.000 Standard Class 1.15 California Paper 2011 North America 45 Office Supplies Los Angeles United States JA-159704 Joseph Airdo 0 US 1 2011-11-12 00:00:00.000 CA-2011-151295 High OFF-PA-10001947 Xerox 1974 5.8604 2 West 33709 12 Consumer 2011-11-16 00:00:00.000 Standard Class 0.92 California Paper 2011 North America 46 Office Supplies Los Angeles United States SP-209204 Susan Pistek 0 US 1 2011-11-22 00:00:00.000 CA-2011-135090 High OFF-PA-10002245 Xerox 1895 24.219 9 West 35267 54 Consumer 2011-11-26 00:00:00.000 Standard Class 6.98 California Paper 2011 North America 48 Office Supplies Los Angeles United States RL-196154 Rob Lucas 0 US 1 2011-12-05 00:00:00.000 CA-2011-133830 Medium OFF-PA-10001363 Xerox 1933 23.0864 4 West 38866 49 Consumer 2011-12-10 00:00:00.000 Standard Class 1.99 California Paper 2011 North America 50 Office Supplies Los Angeles United States KD-163454 Katherine Ducich 0 US 1 2011-12-13 00:00:00.000 CA-2011-113579 High OFF-PA-10001457 White GlueTop Scratch Pads 41.5104 6 West 33788 90 Consumer 2011-12-15 00:00:00.000 Second Class 8.53 California Paper 2011 North America 51 Office Supplies Los Angeles United States JM-161954 Justin MacKendrick 0 US 1 2012-02-15 00:00:00.000 CA-2012-116092 Medium OFF-PA-10004285 Xerox 1959 6.4128 2 West 33544 13 Consumer 2012-02-18 00:00:00.000 Second Class 1 California Paper 2012 North America 7 Office Supplies Los Angeles United States JM-161954 Justin MacKendrick 0 US 1 2012-02-15 00:00:00.000 CA-2012-116092 Medium OFF-PA-10000477 Xerox 22 9.3312 3 West 33548 19 Consumer 2012-02-18 00:00:00.000 Second Class 0.06 California Paper 2012 North America 7 Office Supplies Los Angeles United States RD-195854 Rob Dowd 0 US 1 2012-02-16 00:00:00.000 CA-2012-121776 High OFF-PA-10001970 Xerox 1881 17.3148 3 West 39431 37 Consumer 2012-02-21 00:00:00.000 Standard Class 4.04 California Paper 201

In [0]:
'''
dica: usar quote e escape para evitar que strings com / e "," não sejam considerados como quebra de linha em arquivos csv
'''

Out[35]: '\ndica: usar quote e escape para evitar que strings com / e "," não sejam considerados como quebra de linha em arquivos csv\n'

In [0]:
df.printSchema() 

root
 |-- Category: string (nullable = true)
 |-- City: string (nullable = true)
 |-- Country: string (nullable = true)
 |-- Customer.ID: string (nullable = true)
 |-- Customer.Name: string (nullable = true)
 |-- Discount: string (nullable = true)
 |-- Market: string (nullable = true)
 |-- 记录数: string (nullable = true)
 |-- Order.Date: string (nullable = true)
 |-- Order.ID: string (nullable = true)
 |-- Order.Priority: string (nullable = true)
 |-- Product.ID: string (nullable = true)
 |-- Product.Name: string (nullable = true)
 |-- Profit: string (nullable = true)
 |-- Quantity: string (nullable = true)
 |-- Region: string (nullable = true)
 |-- Row.ID: string (nullable = true)
 |-- Sales: string (nullable = true)
 |-- Segment: string (nullable = true)
 |-- Ship.Date: string (nullable = true)
 |-- Ship.Mode: string (nullable = true)
 |-- Shipping.Cost: string (nullable = true)
 |-- State: string (nullable = true)
 |-- Sub.Category: string (nullable = true)
 |-- Year: string (nullable

In [0]:
df.write.format("delta").mode("overwrite").saveAsTable("bronze.superstore")

In [0]:
df_silver = spark.read.format("delta").table("bronze.superstore")
df_silver.printSchema() 


root
 |-- Category: string (nullable = true)
 |-- City: string (nullable = true)
 |-- Country: string (nullable = true)
 |-- Customer.ID: string (nullable = true)
 |-- Customer.Name: string (nullable = true)
 |-- Discount: string (nullable = true)
 |-- Market: string (nullable = true)
 |-- 记录数: string (nullable = true)
 |-- Order.Date: string (nullable = true)
 |-- Order.ID: string (nullable = true)
 |-- Order.Priority: string (nullable = true)
 |-- Product.ID: string (nullable = true)
 |-- Product.Name: string (nullable = true)
 |-- Profit: string (nullable = true)
 |-- Quantity: string (nullable = true)
 |-- Region: string (nullable = true)
 |-- Row.ID: string (nullable = true)
 |-- Sales: string (nullable = true)
 |-- Segment: string (nullable = true)
 |-- Ship.Date: string (nullable = true)
 |-- Ship.Mode: string (nullable = true)
 |-- Shipping.Cost: string (nullable = true)
 |-- State: string (nullable = true)
 |-- Sub.Category: string (nullable = true)
 |-- Year: string (nullable

In [0]:
'''Renomear o nome das tabelas tirando os caracteres especiais'''

Out[39]: 'Renomear o nome das tabelas tirando os caracteres especiais'

In [0]:
for column in df_silver.columns:
   df_silver= df_silver.withColumnRenamed(column, column.replace(".", "_"))

df_silver.printSchema()
display(df_silver.head(5))


root
 |-- Category: string (nullable = true)
 |-- City: string (nullable = true)
 |-- Country: string (nullable = true)
 |-- Customer_ID: string (nullable = true)
 |-- Customer_Name: string (nullable = true)
 |-- Discount: double (nullable = true)
 |-- Market: string (nullable = true)
 |-- 记录数: string (nullable = true)
 |-- Order_Date: string (nullable = true)
 |-- Order_ID: string (nullable = true)
 |-- Order_Priority: string (nullable = true)
 |-- Product_ID: string (nullable = true)
 |-- Product_Name: string (nullable = true)
 |-- Profit: double (nullable = true)
 |-- Quantity: integer (nullable = true)
 |-- Region: string (nullable = true)
 |-- Row_ID: long (nullable = true)
 |-- Sales: integer (nullable = true)
 |-- Segment: string (nullable = true)
 |-- Ship_Date: timestamp (nullable = true)
 |-- Ship_Mode: string (nullable = true)
 |-- Shipping_Cost: double (nullable = true)
 |-- State: string (nullable = true)
 |-- Sub_Category: string (nullable = true)
 |-- Year: integer (null

Category City Country Customer_ID Customer_Name Discount Market 记录数 Order_Date Order_ID Order_Priority Product_ID Product_Name Profit Quantity Region Row_ID Sales Segment Ship_Date Ship_Mode Shipping_Cost State Sub_Category Year Market2 weeknum Office Supplies Los Angeles United States LS-172304 Lycoris Saunders 0.0 US 1 2011-01-07 00:00:00.000 CA-2011-130813 High OFF-PA-10002005 Xerox 225 9.3312 3 West 36624 19 Consumer 2011-01-09T00:00:00.000+0000 Second Class 4.37 California Paper 2011 North America 2 Office Supplies Los Angeles United States MV-174854 Mark Van Huff 0.0 US 1 2011-01-21 00:00:00.000 CA-2011-148614 Medium OFF-PA-10002893 Wirebound Service Call Books, 5 1/2" x 4" 9.2928 2 West 37033 19 Consumer 2011-01-26T00:00:00.000+0000 Standard Class 0.94 California Paper 2011 North America 4 Office Supplies Los Angeles United States CS-121304 Chad Sievert 0.0 US 1 2011-08-05 00:00:00.000 CA-2011-118962 Medium OFF-PA-10000659 Adams Phone Message Book, Professional, 400 Message Capacity, 5 3/6” x 11” 9.8418 3 West 31468 21 Consumer 2011-08-09T00:00:00.000+0000 Standard Class 1.81 California Paper 2011 North America 32 Office Supplies Los Angeles United States CS-121304 Chad Sievert 0.0 US 1 2011-08-05 00:00:00.000 CA-2011-118962 Medium OFF-PA-10001144 Xerox 1913 53.2608 2 West 31469 111 Consumer 2011-08-09T00:00:00.000+0000 Standard Class 4.59 California Paper 2011 North America 32 Office Supplies Los Angeles United States AP-109154 Arthur Prichep 0.0 US 1 2011-09-29 00:00:00.000 CA-2011-146969 High OFF-PA-10002105 Xerox 223 3.1104 1 West 32440 6 Consumer 2011-10-03T00:00:00.000+0000 Standard Class 1.32 California Paper 2011 North America 40

In [0]:
'''
Definir os tipos certos de dados.
'''

Out[41]: '\nDefinir os tipos certos de dados.\n'

In [0]:
cast_types = {
    "Year": "int",
    "Sales": "int",
    "weeknum": "int",
    "Shipping_Cost": "double",
    "Row_ID": "bigint",
    "Quantity": "int",
    "Profit": "double",
    "Discount": "double",
    "Ship_Date": "timestamp"
}

for column, dtype in cast_types.items():
    df_silver = df_silver.withColumn(column, col(column).cast(dtype))

df_silver.printSchema()


root
 |-- Category: string (nullable = true)
 |-- City: string (nullable = true)
 |-- Country: string (nullable = true)
 |-- Customer_ID: string (nullable = true)
 |-- Customer_Name: string (nullable = true)
 |-- Discount: double (nullable = true)
 |-- Market: string (nullable = true)
 |-- 记录数: string (nullable = true)
 |-- Order_Date: string (nullable = true)
 |-- Order_ID: string (nullable = true)
 |-- Order_Priority: string (nullable = true)
 |-- Product_ID: string (nullable = true)
 |-- Product_Name: string (nullable = true)
 |-- Profit: double (nullable = true)
 |-- Quantity: integer (nullable = true)
 |-- Region: string (nullable = true)
 |-- Row_ID: long (nullable = true)
 |-- Sales: integer (nullable = true)
 |-- Segment: string (nullable = true)
 |-- Ship_Date: timestamp (nullable = true)
 |-- Ship_Mode: string (nullable = true)
 |-- Shipping_Cost: double (nullable = true)
 |-- State: string (nullable = true)
 |-- Sub_Category: string (nullable = true)
 |-- Year: integer (null

In [0]:
'''verificar se há registros com valores nulos nas colunas essenciais'''

Out[43]: 'verificar se há registros com valores nulos nas colunas essenciais'

In [0]:
for column in df_silver.columns:
    null = df_silver.select(count(when(col(column).isNull(), column)))
    display(null)

count(CASE WHEN (Category IS NULL) THEN Category END) 0

count(CASE WHEN (City IS NULL) THEN City END) 0

count(CASE WHEN (Country IS NULL) THEN Country END) 0

count(CASE WHEN (Customer_ID IS NULL) THEN Customer_ID END) 0

count(CASE WHEN (Customer_Name IS NULL) THEN Customer_Name END) 0

...

count(CASE WHEN (State IS NULL) THEN State END) 0

count(CASE WHEN (Sub_Category IS NULL) THEN Sub_Category END) 0

count(CASE WHEN (Year IS NULL) THEN Year END) 0

count(CASE WHEN (Market2 IS NULL) THEN Market2 END) 0

count(CASE WHEN (weeknum IS NULL) THEN weeknum END) 0


Exercício 1: Limpeza de Dados
Enunciado:

Crie uma view chamada orders_cleaned que remova registros com valores nulos nas colunas essenciais (order_id, customer_id, product_id, sales, quantity) e adicione uma coluna clean_timestamp com a data/hora atual do processamento.

In [0]:
df_cleaned = df_silver.dropna(subset=["Order_ID", "Customer_ID", "Product_ID", "Sales", "Quantity"])

In [0]:
df_cleaned = df_cleaned.withColumn("clean_timestamp", current_timestamp())

In [0]:
df_cleaned.createOrReplaceTempView("orders_cleaned")

In [0]:
%sql
SELECT * FROM orders_cleaned LIMIT 5;

Category City Country Customer_ID Customer_Name Discount Market 记录数 Order_Date Order_ID Order_Priority Product_ID Product_Name Profit Quantity Region Row_ID Sales Segment Ship_Date Ship_Mode Shipping_Cost State Sub_Category Year Market2 weeknum clean_timestamp Office Supplies Los Angeles United States LS-172304 Lycoris Saunders 0.0 US 1 2011-01-07 00:00:00.000 CA-2011-130813 High OFF-PA-10002005 Xerox 225 9.3312 3 West 36624 19 Consumer 2011-01-09T00:00:00.000+0000 Second Class 4.37 California Paper 2011 North America 2 2025-04-17T14:20:41.445+0000 Office Supplies Los Angeles United States MV-174854 Mark Van Huff 0.0 US 1 2011-01-21 00:00:00.000 CA-2011-148614 Medium OFF-PA-10002893 Wirebound Service Call Books, 5 1/2" x 4" 9.2928 2 West 37033 19 Consumer 2011-01-26T00:00:00.000+0000 Standard Class 0.94 California Paper 2011 North America 4 2025-04-17T14:20:41.445+0000 Office Supplies Los Angeles United States CS-121304 Chad Sievert 0.0 US 1 2011-08-05 00:00:00.000 CA-2011-118962 Medium OFF-PA-10000659 Adams Phone Message Book, Professional, 400 Message Capacity, 5 3/6” x 11” 9.8418 3 West 31468 21 Consumer 2011-08-09T00:00:00.000+0000 Standard Class 1.81 California Paper 2011 North America 32 2025-04-17T14:20:41.445+0000 Office Supplies Los Angeles United States CS-121304 Chad Sievert 0.0 US 1 2011-08-05 00:00:00.000 CA-2011-118962 Medium OFF-PA-10001144 Xerox 1913 53.2608 2 West 31469 111 Consumer 2011-08-09T00:00:00.000+0000 Standard Class 4.59 California Paper 2011 North America 32 2025-04-17T14:20:41.445+0000 Office Supplies Los Angeles United States AP-109154 Arthur Prichep 0.0 US 1 2011-09-29 00:00:00.000 CA-2011-146969 High OFF-PA-10002105 Xerox 223 3.1104 1 West 32440 6 Consumer 2011-10-03T00:00:00.000+0000 Standard Class 1.32 California Paper 2011 North America 40 2025-04-17T14:20:41.445+0000

Crie uma view chamada standardized_orders que padronize:

Nomes de clientes (remova espaços extras e coloque em maiúsculas)
Categorias de produtos (padronize para UPPER CASE)
Valores monetários (arredonde Sales, Profit e shipping_cost para 2 casas decimais)

In [0]:
df_standard = df_silver.select(
    upper(trim("Customer_Name")).alias("Customer_Name"),
    upper("Category").alias("Category"),
    round("Sales", 2).alias("Sales"),
    round("Profit", 2).alias("Profit"),
    round("Shipping_Cost", 2).alias("Shipping_Cost")
)

In [0]:
df_standard.createOrReplaceTempView("standardized_orders")

In [0]:
%sql
SELECT * FROM standardized_orders LIMIT 5;

Customer_Name Category Sales Profit Shipping_Cost LYCORIS SAUNDERS OFFICE SUPPLIES 19 9.33 4.37 MARK VAN HUFF OFFICE SUPPLIES 19 9.29 0.94 CHAD SIEVERT OFFICE SUPPLIES 21 9.84 1.81 CHAD SIEVERT OFFICE SUPPLIES 111 53.26 4.59 ARTHUR PRICHEP OFFICE SUPPLIES 6 3.11 1.32

Adicione uma coluna order_month extraindo o mês da data do pedido e uma coluna is_profitable que seja TRUE quando Profit > 0.

In [0]:
df_order = df_silver.withColumn(
    "order_month", month(col("Order_Date"))
).withColumn(
    "is_profitable", col("Profit") > 0
)

display(df_order.head(5))

Category City Country Customer_ID Customer_Name Discount Market 记录数 Order_Date Order_ID Order_Priority Product_ID Product_Name Profit Quantity Region Row_ID Sales Segment Ship_Date Ship_Mode Shipping_Cost State Sub_Category Year Market2 weeknum order_month is_profitable Office Supplies Los Angeles United States LS-172304 Lycoris Saunders 0.0 US 1 2011-01-07 00:00:00.000 CA-2011-130813 High OFF-PA-10002005 Xerox 225 9.3312 3 West 36624 19 Consumer 2011-01-09T00:00:00.000+0000 Second Class 4.37 California Paper 2011 North America 2 1 true Office Supplies Los Angeles United States MV-174854 Mark Van Huff 0.0 US 1 2011-01-21 00:00:00.000 CA-2011-148614 Medium OFF-PA-10002893 Wirebound Service Call Books, 5 1/2" x 4" 9.2928 2 West 37033 19 Consumer 2011-01-26T00:00:00.000+0000 Standard Class 0.94 California Paper 2011 North America 4 1 true Office Supplies Los Angeles United States CS-121304 Chad Sievert 0.0 US 1 2011-08-05 00:00:00.000 CA-2011-118962 Medium OFF-PA-10000659 Adams Phone Message Book, Professional, 400 Message Capacity, 5 3/6” x 11” 9.8418 3 West 31468 21 Consumer 2011-08-09T00:00:00.000+0000 Standard Class 1.81 California Paper 2011 North America 32 8 true Office Supplies Los Angeles United States CS-121304 Chad Sievert 0.0 US 1 2011-08-05 00:00:00.000 CA-2011-118962 Medium OFF-PA-10001144 Xerox 1913 53.2608 2 West 31469 111 Consumer 2011-08-09T00:00:00.000+0000 Standard Class 4.59 California Paper 2011 North America 32 8 true Office Supplies Los Angeles United States AP-109154 Arthur Prichep 0.0 US 1 2011-09-29 00:00:00.000 CA-2011-146969 High OFF-PA-10002105 Xerox 223 3.1104 1 West 32440 6 Consumer 2011-10-03T00:00:00.000+0000 Standard Class 1.32 California Paper 2011 North America 40 9 true

In [0]:
df_order.write.format("delta").mode("overwrite").saveAsTable("silver.superstore")

Crie uma tabela agregada sales_by_category que mostre o total de vendas e lucro por categoria de produto.

In [0]:
df_sales_by_category = df_silver.groupBy("Category").agg(
    sum("Sales").alias("total de vendas"),
    sum("Profit").alias("lucro por categoria de produto")
)

display(df_sales_by_category)

Category total de vendas lucro por categoria de produto Office Supplies 3787330 518473.83429999993 Furniture 4110884 285204.7237999993 Technology 4744691 663778.7331800003

Crie uma view recent_orders filtrando apenas pedidos dos últimos 2 anos e particione os dados por ano e mês para otimização.

In [0]:
df_order.write \
    .format("delta") \
    .partitionBy("Year") \
    .mode("overwrite") \
    .option("mergeSchema", "True")\
    .saveAsTable("silver.order_ano")

In [0]:
df_order.write \
    .format("delta") \
    .partitionBy("order_month") \
    .mode("overwrite") \
    .option("mergeSchema", "True")\
    .saveAsTable("silver.order_mes")

In [0]:
%sql
SELECT DISTINCT Year FROM silver.order_ano;

Year 2013 2014 2012 2011

In [0]:
df_order_last_years = spark.read.format("delta").table("silver.order_ano")

In [0]:
df_years = df_order_last_years.select('Year').distinct().orderBy(col("Year").desc()).limit(2).collect()

years_list = []
for year in df_years:
    years_list.append(year['Year'])

print(years_list)


[2014, 2013]


In [0]:
df_recent_orders = df_order_last_years.filter(col("Year").isin(years_list)) #isin espera uma lista, logo, precisei fazer um for e usar collect para transformar em row(Year=2013)

In [0]:
df_recent_orders.createOrReplaceTempView("recent_orders")

In [0]:
%sql
SELECT * FROM recent_orders LIMIT 5;

Category City Country Customer_ID Customer_Name Discount Market Order_Date Order_ID Order_Priority Product_ID Product_Name Profit Quantity Region Row_ID Sales Segment Ship_Date Ship_Mode Shipping_Cost State Sub_Category Year Market2 weeknum order_month is_profitable 记录数 Office Supplies Los Angeles United States SW-202454 Scot Wooten 0.0 US 2013-03-13 00:00:00.000 US-2013-119270 Medium OFF-PA-10004022 Hammermill Color Copier Paper (28Lb. and 96 Bright) 8.991 2 West 39776 20 Consumer 2013-03-17T00:00:00.000+0000 Standard Class 1.3 California Paper 2013 North America 11 3 true 1 Office Supplies Los Angeles United States CC-122204 Chris Cortes 0.0 US 2013-03-29 00:00:00.000 CA-2013-131380 Critical OFF-PA-10001243 Xerox 1983 2.9302 1 West 38455 6 Consumer 2013-04-01T00:00:00.000+0000 Second Class 1.82 California Paper 2013 North America 13 3 true 1 Office Supplies Los Angeles United States LC-171404 Logan Currie 0.0 US 2013-04-09 00:00:00.000 CA-2013-130477 High OFF-PA-10002947 Xerox 1923 9.6192 3 West 32200 20 Consumer 2013-04-13T00:00:00.000+0000 Standard Class 2.92 California Paper 2013 North America 15 4 true 1 Office Supplies Los Angeles United States LC-171404 Logan Currie 0.0 US 2013-04-09 00:00:00.000 CA-2013-130477 High OFF-PA-10000019 Xerox 1931 6.2208 2 West 32202 13 Consumer 2013-04-13T00:00:00.000+0000 Standard Class 2.28 California Paper 2013 North America 15 4 true 1 Office Supplies Los Angeles United States JF-152954 Jason Fortune- 0.0 US 2013-04-13 00:00:00.000 CA-2013-163594 Medium OFF-PA-10000809 Xerox 206 9.3312 3 West 38657 19 Consumer 2013-04-15T00:00:00.000+0000 First Class 1.77 California Paper 2013 North America 15 4 true 1

In [0]:
%sql
SELECT DISTINCT Year FROM  recent_orders; 

Year 2013 2014

Baseado na tabela silver gerada, identifique e crie as tabelas de dimensões e fatos

In [0]:
df_gold = spark.read.format("delta").table("silver.superstore")

In [0]:
display(df_gold.head(2))

Category City Country Customer_ID Customer_Name Discount Market 记录数 Order_Date Order_ID Order_Priority Product_ID Product_Name Profit Quantity Region Row_ID Sales Segment Ship_Date Ship_Mode Shipping_Cost State Sub_Category Year Market2 weeknum order_month is_profitable Office Supplies Los Angeles United States LS-172304 Lycoris Saunders 0.0 US 1 2011-01-07 00:00:00.000 CA-2011-130813 High OFF-PA-10002005 Xerox 225 9.3312 3 West 36624 19 Consumer 2011-01-09T00:00:00.000+0000 Second Class 4.37 California Paper 2011 North America 2 1 true Office Supplies Los Angeles United States MV-174854 Mark Van Huff 0.0 US 1 2011-01-21 00:00:00.000 CA-2011-148614 Medium OFF-PA-10002893 Wirebound Service Call Books, 5 1/2" x 4" 9.2928 2 West 37033 19 Consumer 2011-01-26T00:00:00.000+0000 Standard Class 0.94 California Paper 2011 North America 4 1 true

In [0]:
df_gold.printSchema()

root
 |-- Category: string (nullable = true)
 |-- City: string (nullable = true)
 |-- Country: string (nullable = true)
 |-- Customer_ID: string (nullable = true)
 |-- Customer_Name: string (nullable = true)
 |-- Discount: double (nullable = true)
 |-- Market: string (nullable = true)
 |-- 记录数: string (nullable = true)
 |-- Order_Date: string (nullable = true)
 |-- Order_ID: string (nullable = true)
 |-- Order_Priority: string (nullable = true)
 |-- Product_ID: string (nullable = true)
 |-- Product_Name: string (nullable = true)
 |-- Profit: double (nullable = true)
 |-- Quantity: integer (nullable = true)
 |-- Region: string (nullable = true)
 |-- Row_ID: long (nullable = true)
 |-- Sales: integer (nullable = true)
 |-- Segment: string (nullable = true)
 |-- Ship_Date: timestamp (nullable = true)
 |-- Ship_Mode: string (nullable = true)
 |-- Shipping_Cost: double (nullable = true)
 |-- State: string (nullable = true)
 |-- Sub_Category: string (nullable = true)
 |-- Year: integer (null

In [0]:
df_dim_client = df_gold.select(
    "Customer_ID", "Customer_Name", "Segment"
).distinct()  # ok

In [0]:
df_dim_client.write.format("delta").mode("overwrite").saveAsTable("gold.df_dim_client")

In [0]:
df_dim_product = df_gold.select(
    "Product_ID", "Product_Name", "Category", "Sub_Category"
).distinct()  # ok

In [0]:
df_dim_product.write.format("delta").mode("overwrite").saveAsTable("gold.df_dim_produto")

In [0]:
df_dim_local = df_gold.select(
    "City", "State", "Country", "Region", "Market", "Market2"
).distinct()  # ok

In [0]:
df_dim_local.write.format("delta").mode("overwrite").saveAsTable("gold.df_dim_local")

In [0]:
df_dim_tempo = df_gold.select(
    "Order_Date", "Year", "weeknum", "order_month"
).distinct()  # ok


In [0]:
df_dim_tempo.write.format("delta").mode("overwrite").saveAsTable("gold.df_dim_tempo")

In [0]:
df_fato = df_gold.select(
    "Order_ID", 
    "Customer_ID", 
    "Product_ID", 
    "Order_Date",
    "Ship_Date",
    "Sales", 
    "Profit", 
    "Quantity", 
    "Discount", 
    "Shipping_Cost", 
    "is_profitable"
)

In [0]:
df_fato.write.format("delta").mode("overwrite").saveAsTable("gold.df_fato")

Crie uma análise RFM (Recência, Frequência, Valor Monetário) dos clientes calculando:

Recência: dias desde o último pedido
Frequência: número total de pedidos
Valor Monetário: valor total gasto

In [0]:
date_recent = df_gold.agg(max("Order_Date")).collect()[0][0] 
display(date_recent)

'2014-12-31 00:00:00.000'

In [0]:
df_rfm = df_gold.groupBy("Customer_ID").agg(
    datediff(lit(date_recent), max("Order_Date")).alias("Recencia"),
    countDistinct("Order_ID").alias("Frequencia"),
    sum("Sales").alias("ValorMonetario")
)

display(df_rfm)


Customer_ID Recencia Frequencia ValorMonetario AA-103151 8 5 1445 AA-103152 13 7 6105 AA-103153 694 2 633 AA-103154 184 5 5565 AA-103751 6 4 2407 AA-103752 317 3 560 AA-103753 34 7 1861 AA-103754 19 9 1056 AA-104801 125 5 5946 AA-104802 229 7 5253 AA-104803 236 4 4704 AA-104804 259 4 1792 AA-106451 28 12 5264 AA-106452 233 9 2730 AA-106453 55 9 2263 AA-106454 55 6 5087 AA-3151 153 1 11 AA-3152 2 6 2234 AA-3751 299 4 365 AA-3752 825 1 27 AA-3753 253 3 261 AA-4801 875 2 496 AA-4802 937 1 1085 AA-4803 314 2 482 AA-6451 60 8 1503 AA-6452 51 3 465 AB-100151 113 9 10662 AB-100152 252 12 6116 AB-100153 16 8 2375 AB-100154 415 3 887 AB-100601 81 9 2107 AB-100602 226 5 3345 AB-100603 42 10 5210 AB-100604 54 8 7757 AB-101051 216 7 4309 AB-101052 27 6 2949 AB-101053 32 10 1234 AB-101054 41 10 14476 AB-101501 110 4 429 AB-101502 103 6 9139 AB-101503 35 9 2523 AB-101504 41 5 969 AB-101651 389 5 3435 AB-101652 13 11 6437 AB-101653 60 5 668 AB-101654 25 8 1114 AB-102551 190 7 4277 AB-102552 256 6 949 AB-102553 5 9 4644 AB-102554 166 9 914 AB-1051 402 2 97 AB-1052 230 1 64 AB-1053 43 4 1996 AB-106001 240 9 7148 AB-106002 337 6 4276 AB-106003 84 3 377 AB-106004 50 4 1515 AB-1501 398 4 3145 AB-151 412 2 2125 AB-152 503 3 2481 AB-1651 30 1 160 AB-1652 709 1 411 AB-1653 16 4 828 AB-2551 174 5 4083 AB-2552 43 1 283 AB-2553 120 2 313 AB-6001 7 3 1384 AB-6002 875 2 4027 AB-601 35 3 1483 AB-602 133 6 287 AC-104201 219 5 4086 AC-104202 462 7 1033 AC-104203 6 9 4561 AC-104204 232 3 926 AC-104501 8 5 7610 AC-104502 5 4 2295 AC-104503 196 3 694 AC-104504 11 7 5529 AC-106151 12 11 5753 AC-106152 40 5 2738 AC-106153 36 8 1699 AC-106154 6 5 2538 AC-106601 63 4 1175 AC-106602 151 6 2234 AC-106603 2 6 2189 AC-106604 282 5 658 AC-4201 13 6 841 AC-4202 386 3 849 AC-4501 336 3 670 AC-4502 919 2 147 AC-4503 181 2 210 AC-6151 509 3 1706 AC-6152 92 4 593 AC-6601 119 3 2666 AC-6602 412 1 10 AD-101801 92 8 9209 AD-101802 376 5 1001 AD-101803 331 6 1541 AD-101804 29 8 6106 AD-1801 196 1 12 AD-1802 5 2 669 AF-108701 6 14 10793 AF-108702 105 6 7808 AF-108703 426 9 5832 AF-108704 41 7 2052 AF-108851 76 10 8347 AF-108852 162 13 5880 AF-108853 53 8 4621 AF-108854 415 4 862 AF-8701 12 4 672 AF-8702 765 1 125 AF-8703 5 4 901 AF-8851 203 1 139 AF-8852 167 1 215 AG-102701 65 7 4771 AG-102702 196 4 1663 AG-102703 40 9 1622 AG-102704 278 5 2584 AG-103001 27 5 3212 AG-103002 72 7 6071 AG-103003 2 8 3364 AG-103004 118 4 367 AG-103301 172 5 4208 AG-103302 149 9 3590 AG-103303 182 10 6078 AG-103304 8 5 662 AG-103901 240 2 2228 AG-103902 413 4 2646 AG-103903 189 8 3380 AG-103904 114 5 201 AG-104951 167 6 3451 AG-104952 128 11 7461 AG-104953 200 4 2110 AG-104954 78 8 2356 AG-105251 134 3 324 AG-105252 37 8 4071 AG-105253 12 5 2620 AG-105254 845 4 1455 AG-106751 769 3 3644 AG-106752 47 7 2284 AG-106753 400 4 3606 AG-106754 97 7 3489 AG-107651 376 4 1586 AG-107652 92 6 2159 AG-107653 28 13 5913 AG-107654 77 4 170 AG-109001 117 8 5035 AG-109002 372 8 3108 AG-109003 57 3 5519 AG-109004 96 10 4511 AG-2701 163 5 1997 AG-2702 519 1 296 AG-2703 13 2 486 AG-3001 145 2 866 AG-3002 98 4 835 AG-3301 2 6 513 AG-3302 14 1 20 AG-3901 1120 2 414 AG-3902 112 2 59 AG-4951 205 3 469 AG-4952 48 2 52 AG-4953 69 6 482 AG-5251 15 6 802 AG-5252 728 1 2067 AG-6751 173 6 774 AG-6752 270 4 1595 AG-7651 579 4 769 AG-7652 114 4 1090 AG-9001 23 4 1698 AH-100301 410 6 4154 AH-100302 28 8 3973 AH-100303 158 6 4568 AH-100304 12 7 1744 AH-100751 2 9 7291 AH-100752 30 9 4526 AH-100753 230 6 3044 AH-100754 34 10 3251 AH-101201 471 3 558 AH-101202 113 6 3590 AH-101203 306 6 4044 AH-101204 60 7 1736 AH-101951 49 6 3839 AH-101952 92 9 1833 AH-101953 51 6 5370 AH-101954 55 4 1588 AH-102101 470 2 1111 AH-102102 102 11 7417 AH-102103 7 12 7031 AH-102104 6 9 4805 AH-104651 86 6 2183 AH-104652 480 2 251 AH-104653 70 7 3621 AH-104654 230 5 2495 AH-105851 187 9 6205 AH-105852 183 5 1615 AH-105853 398 4 567 AH-105854 21 4 738 AH-106901 145 6 4163 AH-106902 30 9 3514 AH-106903 379 4 710 AH-106904 410 12 7889 AH-1201 599 3 1476 AH-1

Analise a sazonalidade das vendas por mês e categoria, criando uma tabela com as vendas médias mensais por categoria.


In [0]:
df_seasonality_month= spark.table("silver.order_mes") 

In [0]:
df_seasonality = df_seasonality_month.groupBy("Category", "order_month").agg(
    round(mean("Sales"), 2).alias("Media_Vendas")
).orderBy("Category", "order_month")

display(df_seasonality)


Category order_month Media_Vendas Furniture 1 467.4 Furniture 2 448.83 Furniture 3 436.47 Furniture 4 368.6 Furniture 5 395.9 Furniture 6 410.84 Furniture 7 366.89 Furniture 8 448.87 Furniture 9 418.85 Furniture 10 412.36 Furniture 11 408.72 Furniture 12 423.02 Office Supplies 1 137.87 Office Supplies 2 118.74 Office Supplies 3 122.68 Office Supplies 4 121.4 Office Supplies 5 120.41 Office Supplies 6 113.8 Office Supplies 7 122.82 Office Supplies 8 126.08 Office Supplies 9 116.4 Office Supplies 10 113.47 Office Supplies 11 121.93 Office Supplies 12 124.63 Technology 1 450.46 Technology 2 443.45 Technology 3 483.9 Technology 4 426.54 Technology 5 481.13 Technology 6 460.81 Technology 7 453.24 Technology 8 493.64 Technology 9 458.08 Technology 10 531.97 Technology 11 457.87 Technology 12 453.67

Identifique os 10 produtos mais rentáveis (maior margem de lucro) e os 10 menos rentáveis.

In [0]:
df_high_profit = (
    df_gold
    .groupBy("Product_ID")
    .agg(max("Profit").alias("maior margem de lucro"))
    .limit(10)
    .orderBy(desc("maior margem de lucro"))
)

display(df_high_profit)

Product_ID maior margem de lucro OFF-ST-10000624 441.36 OFF-ROG-10001340 144.36 OFF-EN-10004410 98.28 OFF-AP-10002495 55.845 OFF-NOV-10000141 37.44 OFF-PA-10004735 21.7728 OFF-PA-10002615 14.2002 OFF-EN-10002600 12.744 OFF-AR-10003504 9.9296 OFF-AVE-10002892 0.0

In [0]:
df_low_profit = (
    df_gold
    .groupBy("Product_ID")
    .agg(min("Profit").alias("menor margem de lucro"))
    .limit(10)
    .orderBy(asc("menor margem de lucro"))
)

display(df_low_profit)


Product_ID menor margem de lucro OFF-ROG-10001340 -243.6 OFF-ST-10000624 -109.26 OFF-AVE-10002892 -39.522 OFF-EN-10004410 0.0 OFF-PA-10002615 1.1466 OFF-AR-10003504 1.1556 OFF-EN-10002600 1.652 OFF-PA-10004735 3.6288 OFF-NOV-10000141 6.24 OFF-AP-10002495 12.41

Segmentar clientes em categorias (Bronze, Prata, Ouro) baseado no valor total gasto:

Bronze: < $1000
Prata: 1000 − 1000−5000
Ouro: > $5000

In [0]:
df_segment_client = df_gold.withColumn(
    "Nivel", 
    when(col("Sales") < 1000, "bronze")
    .when((col("Sales") >= 1000) & (col("Sales") <= 5000), "prata")
    .when(col("Sales") > 5000, "ouro")
    .otherwise("sem classificação")
)

display(df_segment_client.head(5))

Category City Country Customer_ID Customer_Name Discount Market 记录数 Order_Date Order_ID Order_Priority Product_ID Product_Name Profit Quantity Region Row_ID Sales Segment Ship_Date Ship_Mode Shipping_Cost State Sub_Category Year Market2 weeknum order_month is_profitable Nivel Office Supplies Los Angeles United States LS-172304 Lycoris Saunders 0.0 US 1 2011-01-07 00:00:00.000 CA-2011-130813 High OFF-PA-10002005 Xerox 225 9.3312 3 West 36624 19 Consumer 2011-01-09T00:00:00.000+0000 Second Class 4.37 California Paper 2011 North America 2 1 true bronze Office Supplies Los Angeles United States MV-174854 Mark Van Huff 0.0 US 1 2011-01-21 00:00:00.000 CA-2011-148614 Medium OFF-PA-10002893 Wirebound Service Call Books, 5 1/2" x 4" 9.2928 2 West 37033 19 Consumer 2011-01-26T00:00:00.000+0000 Standard Class 0.94 California Paper 2011 North America 4 1 true bronze Office Supplies Los Angeles United States CS-121304 Chad Sievert 0.0 US 1 2011-08-05 00:00:00.000 CA-2011-118962 Medium OFF-PA-10000659 Adams Phone Message Book, Professional, 400 Message Capacity, 5 3/6” x 11” 9.8418 3 West 31468 21 Consumer 2011-08-09T00:00:00.000+0000 Standard Class 1.81 California Paper 2011 North America 32 8 true bronze Office Supplies Los Angeles United States CS-121304 Chad Sievert 0.0 US 1 2011-08-05 00:00:00.000 CA-2011-118962 Medium OFF-PA-10001144 Xerox 1913 53.2608 2 West 31469 111 Consumer 2011-08-09T00:00:00.000+0000 Standard Class 4.59 California Paper 2011 North America 32 8 true bronze Office Supplies Los Angeles United States AP-109154 Arthur Prichep 0.0 US 1 2011-09-29 00:00:00.000 CA-2011-146969 High OFF-PA-10002105 Xerox 223 3.1104 1 West 32440 6 Consumer 2011-10-03T00:00:00.000+0000 Standard Class 1.32 California Paper 2011 North America 40 9 true bronze


Ticket médio por pedido
Média de produtos por pedido
Taxa de crescimento mensal de vendas

In [0]:
average_order_value = df_gold.agg(
    (sum(col("Sales")) / countDistinct(col("Order_ID"))).alias("ticket_medio_pedido")
)

display(average_order_value)

ticket_medio_pedido 505.0091871380068

In [0]:
mean_product = df_gold.groupBy("Order_ID") \
    .agg(sum("Quantity").alias("total_qtd_product")) \
    .agg(avg("total_qtd_product").alias("media_produtos_pedido"))

display(mean_product)

media_produtos_pedido 7.122508488116637

In [0]:
janela = Window.orderBy("Year", "order_month")
# Para acessar linhas anteriores ou posteriores de uma forma estruturada (ordenada por year e month)

In [0]:
sales_month = df_order.groupBy("Year", "order_month") \
    .agg(sum("Sales").alias("total_vendas"))

In [0]:
sales_month = sales_month.withColumn(
    "vendas_mes_anterior", 
    lag("total_vendas").over(janela)
)
#lag usado para pegar uma coluna desejada e fazer o valor anterior dela em cada linha.

In [0]:
sales_month = sales_month.withColumn(
    "taxa de crescimento mensal",
    round(
        when(col("vendas_mes_anterior").isNotNull(),
             ((col("total_vendas") - col("vendas_mes_anterior")) / col("vendas_mes_anterior")) * 100)
        .otherwise(0), 2
    )
)

display(sales_month)


Year order_month total_vendas vendas_mes_anterior taxa de crescimento mensal 2011 1 98902 null 0.0 2011 2 91152 98902 -7.84 2011 3 145726 91152 59.87 2011 4 116927 145726 -19.76 2011 5 146762 116927 25.52 2011 6 215214 146762 46.64 2011 7 115518 215214 -46.32 2011 8 207570 115518 79.69 2011 9 290230 207570 39.82 2011 10 199070 290230 -31.41 2011 11 298499 199070 49.95 2011 12 333941 298499 11.87 2012 1 135775 333941 -59.34 2012 2 100521 135775 -25.97 2012 3 163092 100521 62.25 2012 4 161060 163092 -1.25 2012 5 208370 161060 29.37 2012 6 256181 208370 22.95 2012 7 145247 256181 -43.3 2012 8 303158 145247 108.72 2012 9 289390 303158 -4.54 2012 10 252942 289390 -12.59 2012 11 323512 252942 27.9 2012 12 338245 323512 4.55 2013 1 199197 338245 -41.11 2013 2 167247 199197 -16.04 2013 3 198591 167247 18.74 2013 4 177835 198591 -10.45 2013 5 260525 177835 46.5 2013 6 396513 260525 52.2 2013 7 229940 396513 -42.01 2013 8 326491 229940 41.99 2013 9 376626 326491 15.36 2013 10 293423 376626 -22.09 2013 11 373996 293423 27.46 2013 12 405476 373996 8.42 2014 1 241267 405476 -40.5 2014 2 184848 241267 -23.38 2014 3 263110 184848 42.34 2014 4 242781 263110 -7.73 2014 5 288404 242781 18.79 2014 6 401843 288404 39.33 2014 7 258718 401843 -35.62 2014 8 456633 258718 76.5 2014 9 481186 456633 5.38 2014 10 422785 481186 -12.14 2014 11 555312 422785 31.35 2014 12 503154 555312 -9.39

Baseado em sua analise da base de dados, faça analises que você acredite ser importantes para o negocio.

In [0]:
df_segment = df_segment_client.groupBy("Nivel").agg(sum("Sales").alias("total_vendas"))
display(df_segment)

Nivel total_vendas bronze 7835128 ouro 323017 prata 4484760

Databricks visualization. Run in Databricks to view.

In [0]:
df_ticket = df_segment_client.groupBy("Nivel").agg((sum("Sales") / countDistinct("Order_ID")).alias("ticket_medio"))
display(df_ticket)


Nivel ticket_medio bronze 321.2961535307143 ouro 7341.295454545455 prata 1858.5826771653544

Databricks visualization. Run in Databricks to view.

In [0]:
'''
é possível inferir que os clientes bronze realizam um grande volume de compras com valores mais baixos, enquanto os clientes do segmento ouro, compram com menor frequência porém com valores altos.
'''

Out[137]: '\nÉ possível inferir que os clientes fazem muitas compras de valores baixos, enquanto algumas clientes do Nivel ouro compram menos porém mais caro.\n'

In [0]:
df_sales_by_category = df_gold.groupBy("Category").agg(
    sum("Sales").alias("total_vendas"),
    sum("Profit").alias("lucro_por_categoria")
)
display(df_sales_by_category)


Category total_vendas lucro_por_categoria Office Supplies 3787330 518473.83429999993 Furniture 4110884 285204.7237999993 Technology 4744691 663778.7331800003

Databricks visualization. Run in Databricks to view.

In [0]:
df_seasonality_sales = df_seasonality_month.groupBy("order_month").agg(
    round(mean("Sales"), 2).alias("media_vendas")
).orderBy("order_month")

display(df_seasonality_sales)

order_month media_vendas 1 259.77 2 250.82 3 253.88 4 228.53 5 241.28 6 238.18 7 236.71 8 254.8 9 240.57 10 260.18 11 244.61 12 250.84

Databricks visualization. Run in Databricks to view.

In [0]:
df_shipping_cost = df_gold.groupBy("Category").agg(
    sum("Shipping_Cost").alias("custo_envio")
).orderBy(asc("custo_envio"))

display(df_shipping_cost)

Category custo_envio Office Supplies 405448.3449999992 Furniture 440319.4790000006 Technology 507047.879399997

Databricks visualization. Run in Databricks to view.